# Compliance Analysis: 

## Correlation of GHG Intensity Last Year and Reporting Compliance This Year

### Issue #114
Colton Lapp 

November 2024


### Description: 
Does the GHG intensity the year prior help predict reporting non-compliance this year? 
Does the trend of a GHG intensity (i.e. is a building increasing or decreasing its GHG intensity) help predict reporting non-compliance this year? 

I look at the raw data from the Chicago open data portal and use some basic group means and regression modeling. 

### Conclusion:
It doesn't seem like the level of GHG intensity or the trend of GHG intensity help predict compliance at all. 
Building size DOES help predict compliance though. For every million additional square feet, the building is roughly 1.5% less likely to be NON compliant

In [351]:
import pandas as pd
import numpy as np
import plotly.subplots as sp
import plotly.graph_objects as go
import plotly.express as px
import plotly.io as pio
from plotly.subplots import make_subplots
import math
import statsmodels.api as sm 
import os
from pathlib import Path
import json 



pd.set_option('display.max_columns', None)

# Assert that the current working directory is the "analysis" folder



# get static dir for saving images
current_dir = Path.cwd()
project_root = current_dir
while True:
    if os.path.basename(project_root) == 'electrify-chicago':
        print("Success: Found 'electrify-chicago' as the base directory.")
        break
    new_root = os.path.dirname(project_root)
    if new_root == project_root:  # Reached the filesystem root
        raise FileNotFoundError("Error: 'electrify-chicago' directory not found in the path hierarchy.")
    project_root = new_root
static_blog_pth = os.path.join(project_root, 'static', 'blog', 'GHGIntensityPredictCompliance')
os.makedirs(static_blog_pth, exist_ok=True)

expected_dir_name = "analysis"
fig_dir = os.path.join(current_dir, 'output', 'compliance_analysis')

# Check if the current directory is the "analysis" folder
if current_dir.name != expected_dir_name:
    raise AssertionError(f"Expected working directory to be '{expected_dir_name}', but got '{current_dir.name}'.\n"
                         f"Please ensure you are in the correct directory.")

print(f"Current working directory is correctly set to '{current_dir}'.")

Success: Found 'electrify-chicago' as the base directory.
Current working directory is correctly set to '/Users/coltonlapp/Dropbox/My Mac (Coltons-MacBook-Pro.local)/Desktop/Life/ChiHack/electrify-chicago/src/data/analysis'.


## Read in data

In [352]:
# Construct the path to the CSV file (one level above the current directory)
data_path = os.path.join( current_dir.parent, 'dist', 'benchmarking-all-years.csv')

df = pd.read_csv(data_path)

# Create the "reported" column
df['Reported'] = df['GHGIntensity'].notna().astype(int)

print(f"There are {df['ID'].unique().shape[0]} unique building ids")

df['DataYear'] = df['DataYear'].astype(int)

df.head()

There are 3749 unique building ids


ID  DataYear ReportingStatus  GrossFloorArea  TotalGHGEmissions  \
0  252064      2020  Submitted Data         64028.0             1160.9   
1  232458      2020  Submitted Data        627680.0             4871.7   
2  254616      2020  Submitted Data        555524.0             4581.4   
3  103812      2020  Submitted Data        130007.0             1092.1   
4  254073      2020  Submitted Data         83000.0              295.8   

   GHGIntensity  NumberOfBuildings  ChicagoEnergyRating  ENERGYSTARScore  \
0          18.1                1.0                  2.0              NaN   
1           7.8                1.0                  1.0             22.0   
2           8.2                1.0                  2.0             49.0   
3           8.4                1.0                  3.0             61.0   
4           3.6                1.0                  4.0            100.0   

   ElectricityUse  NaturalGasUse  DistrictSteamUse  DistrictChilledWaterUse  \
0       2384738.9            NaN         7438787.0                5594040.1   
1      16397682.8     43537490.6               NaN                      NaN   
2      28606427.7      2199940.1               NaN                      NaN   
3       6489281.3      1493523.2               NaN                      NaN   
4       1614582.3       825006.6               NaN                      NaN   

   AllOtherFuelUse  SiteEUI  SourceEUI  WeatherNormalizedSiteEUI  \
0              NaN    240.8      323.6                     246.0   
1              NaN     95.5      146.0                     100.3   
2              NaN     55.5      148.3                      56.7   
3              NaN     61.4      151.8                      63.0   
4              NaN     29.4       64.9                      29.6   

   WeatherNormalizedSourceEUI  Reported  
0                       329.9         1  
1                       150.7         1  
2                       151.8         1  
3                       154.8         1  
4                        64.3         1

## Read in Building Benchmark Data to get Building Names

In [353]:
names_path = os.path.join( current_dir.parent, 'dist', 'building-benchmarks.csv')

building_names = pd.read_csv(names_path)[['ID', 'PropertyName' ]]
building_names.drop_duplicates(keep='first')
building_names.head()

ID                        PropertyName
0  100001  Presence SMEMC St Elizabeth Campus
1  100002  Clemente Community Academy HS -CPS
2  100019                      Dixon Building
3  100068                       Joffco Square
4  100148          The Jeffery Cyril Building

## Merge names to data

In [354]:
df = pd.merge( df, building_names, how='left', on='ID')
df.head()

ID  DataYear ReportingStatus  GrossFloorArea  TotalGHGEmissions  \
0  252064      2020  Submitted Data         64028.0             1160.9   
1  232458      2020  Submitted Data        627680.0             4871.7   
2  254616      2020  Submitted Data        555524.0             4581.4   
3  103812      2020  Submitted Data        130007.0             1092.1   
4  254073      2020  Submitted Data         83000.0              295.8   

   GHGIntensity  NumberOfBuildings  ChicagoEnergyRating  ENERGYSTARScore  \
0          18.1                1.0                  2.0              NaN   
1           7.8                1.0                  1.0             22.0   
2           8.2                1.0                  2.0             49.0   
3           8.4                1.0                  3.0             61.0   
4           3.6                1.0                  4.0            100.0   

   ElectricityUse  NaturalGasUse  DistrictSteamUse  DistrictChilledWaterUse  \
0       2384738.9            NaN         7438787.0                5594040.1   
1      16397682.8     43537490.6               NaN                      NaN   
2      28606427.7      2199940.1               NaN                      NaN   
3       6489281.3      1493523.2               NaN                      NaN   
4       1614582.3       825006.6               NaN                      NaN   

   AllOtherFuelUse  SiteEUI  SourceEUI  WeatherNormalizedSiteEUI  \
0              NaN    240.8      323.6                     246.0   
1              NaN     95.5      146.0                     100.3   
2              NaN     55.5      148.3                      56.7   
3              NaN     61.4      151.8                      63.0   
4              NaN     29.4       64.9                      29.6   

   WeatherNormalizedSourceEUI  Reported               PropertyName  
0                       329.9         1           Mansueto Library  
1                       150.7         1  Harper Square Cooperative  
2                       151.8         1       Former Coyne College  
3                       154.8         1          400 W Superior St  
4                        64.3         1            Blue Moon Lofts

### Check that every building/year combo exists only once

In [355]:
group_counts = df.groupby(['ID', 'DataYear']).size()

# Assert that the maximum count in any group is at most 1
assert group_counts.max() <= 1, "There are buildings with more than one row in a given year!"

## Analysis: Unique values for GHG Intensity

Conclusion: strange that some values are highly represented while others are not. How are these calculated? 

In [356]:
df['GHGIntensity'].value_counts().sort_values(ascending=False)

GHGIntensity
6.50     311
6.00     301
6.90     300
5.70     299
7.10     297
        ... 
27.35      1
9.41       1
13.06      1
57.35      1
79.70      1
Name: count, Length: 717, dtype: int64

In [357]:
# Round GHG Intensity values to 1 digit
df['GHGIntensity'] = df['GHGIntensity'].round(1)

## Plot Distribution of GHG Intensities

In [358]:
value_counts = df['GHGIntensity'].value_counts().sort_index()


fig = sp.make_subplots( rows=1, cols=2, 
                       column_widths=[.8, .2],
                         horizontal_spacing=.2,
                         subplot_titles = ['', '<i>GHG Intensity Outliers</i>'])


fig.add_trace( go.Histogram(
    x=df['GHGIntensity'],
    #nbinsx=int((df['GHGIntensity'].max() - df['GHGIntensity'].min()) / 0.5),
    xbins = dict(start=0, end=100, size=.5),
    name='Histogram of Values',
    hovertemplate = " %{y} Buildings <br>with GHG Intensity between %{x}<extra></extra>"
        ),
        row=1,col=1
)

fig.add_trace( go.Box(
    y=df['GHGIntensity'] ,name='', boxpoints='outliers',orientation='v',
    hovertext = df['PropertyName'],
    customdata=df['DataYear'],
    hovertemplate = "%{hovertext}<br>GHG Intensity: %{y} in %{customdata}"
    ), row=1,col=2, 
)

fig.update_xaxes(range=[0, 100], row=1,col=1)
fig.update_xaxes( title_text='' , row=1,col=2)

fig.update_yaxes( title_text='GHG Intensity', row=1,col=2)

## Add an outline to the bars
fig.update_traces(marker=dict(line=dict(width=.1, color='black')))

fig.add_annotation(
    x=80,
    y=300,
    text="<i>Some buildings had  <br>outlier GHG intensity levels (up to 800) →</i>",
    showarrow=False,  # No arrow for this annotation
    font=dict(size=10),  # Customize font size
)

# Update layout for better display
fig.update_layout(
    xaxis_title='GHG Intensity',
    yaxis_title='Count',
    showlegend=False,
    title='Distribution of GHG Intensities',
    height=400,
    width=800
)

# Show the plot
pio.show(fig)

for dir in [static_blog_pth, fig_dir]:
    fig.write_html( os.path.join(dir,'distribution_of_GHG_intensity.html'), full_html=True )

## Compliance type counts over time

In [359]:
# Count each new column per year
value_counts = df.groupby('DataYear')['Reported'].value_counts()
non_reporting_counts = value_counts.xs(0, level='Reported')
reporting_counts = value_counts.xs(1, level='Reported')

# Create the figure
fig = go.Figure()

# Add traces for each category
fig.add_trace(go.Scatter(x=reporting_counts.index, y=reporting_counts.values,
                         mode='lines+markers', name='Reported',
                         line=dict(width=4, color='rgba(0, 0,255, 0.7)'),
                         marker=dict(symbol='circle', size=10)))

fig.add_trace(go.Scatter(x=non_reporting_counts.index, y=non_reporting_counts.values,
                         mode='lines+markers', name="Didn't Report",
                         line=dict(width=4, color='rgba(255, 0, 0, 0.7)'),
                         marker=dict(symbol='circle', size=10)))

fig.add_trace( go.Scatter( x=[2018.5, 2019.5, 2019.5, 2018.5, 2018.5], 
                          y=[0, 0, np.max(reporting_counts)*1.2, np.max(reporting_counts)*1.2, 0 ], 
                         fill='toself', mode='lines', name='Covid Data Disruption' )
)

# Update layout
fig.update_layout(title="Count of Buildings That Did/Didn't Report Emissions by Year",
                  xaxis_title='Year of Emissions<br>(One year before data is reported)',
                  yaxis_title='Count of Buildings',
                  legend_title='Category')

# Show the plot
pio.show(fig)


for dir in [static_blog_pth, fig_dir]:
    fig.write_html( os.path.join(dir,'reporting_counts_over_time.html'), full_html=True )



## Analysis: Covid saw temporary drop in building reporting
Buildings report the prior years emissions data the following spring. Thus, 2019's data was supposed to be reported in Spring 2020 but it seems like Covid disrupted this. As a result, many observations of non-reporting are because of Covid. 

For robustness, we will create a subset of the dataframe without the covid data later in this code

## Analysis: Correlation of "GHG Intensity Last Year" and "Compliance This Year"

### First: calculate "GHG Intensity last year"

In [360]:
# Create the new column 'GHGIntensity_last_year'
df['GHGIntensity_LastYear'] = df.apply(
    lambda row: df.loc[
        (df['DataYear'] == row['DataYear'] - 1) & 
        (df['Reported'] == 1) & 
        (df['ID'] == row['ID']),  # Match by id
        'GHGIntensity'
    ].iloc[0] if len(df.loc[
        (df['DataYear'] == row['DataYear'] - 1) & 
        (df['Reported'] == 1) & 
        (df['ID'] == row['ID']),  # Match by id
        'GHGIntensity'
    ]) > 0 else None,
    axis=1
)

# Create the new column 'pct_chng_GHGIntensity_last_year'
df['Chng_GHGIntensity_LastYear'] = df.apply(
    lambda row: (
        (
            df.loc[
                (df['DataYear'] == row['DataYear'] - 1) & 
                (df['Reported'] == 1) & 
                (df['ID'] == row['ID']),  # Match by id
                'GHGIntensity'
            ].iloc[0]

              -

            df.loc[
                (df['DataYear'] == row['DataYear'] - 2) & 
                (df['Reported'] == 1) & 
                (df['ID'] == row['ID']),  # Match by id
                'GHGIntensity'
            ].iloc[0]
        ) 
        
    ) if len(df.loc[
        (df['DataYear'] == row['DataYear'] - 1) & 
        (df['Reported'] == 1) & 
        (df['ID'] == row['ID']),  # Match by id
        'GHGIntensity'
    ]) == 1 and len(df.loc[
        (df['DataYear'] == row['DataYear'] - 2) & 
        (df['Reported'] == 1) & 
        (df['ID'] == row['ID']),  # Match by id
        'GHGIntensity'
    ]) == 1 else None,
    axis=1
)




In [361]:
df.sort_values( ['ID', 'DataYear']).head()[['DataYear', 'ID','GHGIntensity', 'GHGIntensity_LastYear', 'Chng_GHGIntensity_LastYear']]

DataYear      ID  GHGIntensity  GHGIntensity_LastYear  \
8645       2014  100001          21.2                    NaN   
8623       2015  100001          20.7                   21.2   
10018      2016  100001          19.2                   20.7   
13408      2017  100001          18.8                   19.2   
14232      2018  100001          17.4                   18.8   

       Chng_GHGIntensity_LastYear  
8645                          NaN  
8623                          NaN  
10018                        -0.5  
13408                        -1.5  
14232                        -0.4

#### Create subset without Covid data

In [362]:
n_obs_original = df.shape[0]
df_no_covid = df[df['DataYear']!=2019]

print(f"Dropped {n_obs_original - df_no_covid.shape[0] } observations by omitting COVID data in subset of data ({round(100*(n_obs_original - df_no_covid.shape[0])/n_obs_original, 2)}%)")

Dropped 3438 observations by omitting COVID data in subset of data (13.81%)


## Basic Regression Models to Determine Effects of GHG Intensity on Reporting

In [363]:
def linear_prob_model(df, regressors, target):

    # Start with a copy of the DataFrame
    df_cleaned = df.copy()


    # Initialize a dictionary to track dropped rows for each regressor
    dropped_rows = {}

    # Drop rows with missing values for each regressor and track the counts
    nrow_init = df_cleaned.shape[0]
    for regressor in regressors:
        initial_rows = len(df_cleaned)
        df_cleaned = df_cleaned.dropna(subset=[regressor])
        dropped_rows[regressor] = initial_rows - len(df_cleaned)

    # Report the number of dropped rows for each regressor
    for regressor, count in dropped_rows.items():
        print(f"Rows dropped due to missing values in '{regressor}': {count} ({round(100*(count/nrow_init), 1)}%)")

    # Set up the linear probability model
    X = df_cleaned[regressors]
    X = sm.add_constant(X)  # Add a constant for the intercept
    y = df_cleaned[target]

    # Fit the regression model
    model = sm.OLS(y, X).fit()

    # Display the summary of the model
    print(model.summary())

    return model

In [364]:
# Define the binary target column and regressors
df['GrossFloorArea_Mil'] = df['GrossFloorArea']/1000000
df['non_reporting'] = (df['Reported']==0).astype(int)

df_no_covid['GrossFloorArea_Mil'] = df_no_covid['GrossFloorArea']/1000000
df_no_covid['non_reporting'] = (df_no_covid['Reported']==0).astype(int)

target_var = 'non_reporting'
regressors = [
    'GHGIntensity_LastYear',
    'Chng_GHGIntensity_LastYear',
    'GrossFloorArea_Mil'
]

# Define variables
target_var = 'non_reporting'
regressors = [
    'GHGIntensity_LastYear',
    'Chng_GHGIntensity_LastYear',
    'GrossFloorArea_Mil'
]

# Map pretty names for each variable
pretty_names = {
    'non_reporting': 'Non-Reporting',
    'GHGIntensity_LastYear': 'GHG Intensity (Last Year)',
    'Chng_GHGIntensity_LastYear': 'Change in GHG Intensity Last Two Years',
    'GrossFloorArea_Mil': 'Gross Floor Area (Millions)'
}


/var/folders/np/9tdxr2056n39qzb1mpdsjrtc0000gn/T/ipykernel_48115/827364069.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/np/9tdxr2056n39qzb1mpdsjrtc0000gn/T/ipykernel_48115/827364069.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Basic Regression

In [365]:
model = linear_prob_model(df, regressors, target_var)



# Extract regression results
results = {
    "dependent_variable": pretty_names[target_var],  # Pretty name for dependent variable
    "number_of_observations": int(model.nobs),  # Number of observations
    "r_squared": model.rsquared,  # R-squared
    "adj_r_squared": model.rsquared_adj,  # Adjusted R-squared
    "coefficients": {  # Coefficients with pretty names
        pretty_names.get(name, name): coef for name, coef in model.params.items()
    },
    "p_values": {  # P-values with pretty names
        pretty_names.get(name, name): pval for name, pval in model.pvalues.items()
    },
    "confidence_intervals": {  # 95% confidence intervals with pretty names
        pretty_names.get(name, name): list(ci) for name, ci in model.conf_int().iterrows()
    },
    "covariance_type": model.cov_type,  # Covariance type
}



# Save as JSON
for dir in [static_blog_pth, fig_dir]:
    fpath = os.path.join(dir,'regression_results_w_covid.json')
    with open(fpath, "w") as f:
        json.dump(results, f, indent=4)

Rows dropped due to missing values in 'GHGIntensity_LastYear': 8544 (34.3%)
Rows dropped due to missing values in 'Chng_GHGIntensity_LastYear': 5007 (20.1%)
Rows dropped due to missing values in 'GrossFloorArea_Mil': 752 (3.0%)
                            OLS Regression Results                            
Dep. Variable:          non_reporting   R-squared:                       0.001
Model:                            OLS   Adj. R-squared:                  0.000
Method:                 Least Squares   F-statistic:                     2.406
Date:                Wed, 18 Dec 2024   Prob (F-statistic):             0.0653
Time:                        22:37:49   Log-Likelihood:                -3202.1
No. Observations:               10588   AIC:                             6412.
Df Residuals:                   10584   BIC:                             6441.
Df Model:                           3                                         
Covariance Type:            nonrobust                        

## Drop Covid Data

In [366]:
linear_prob_model(df_no_covid, regressors, target_var)

Rows dropped due to missing values in 'GHGIntensity_LastYear': 7840 (36.5%)
Rows dropped due to missing values in 'Chng_GHGIntensity_LastYear': 4829 (22.5%)
Rows dropped due to missing values in 'GrossFloorArea_Mil': 0 (0.0%)
                            OLS Regression Results                            
Dep. Variable:          non_reporting   R-squared:                       0.003
Model:                            OLS   Adj. R-squared:                  0.003
Method:                 Least Squares   F-statistic:                     8.934
Date:                Wed, 18 Dec 2024   Prob (F-statistic):           6.60e-06
Time:                        22:37:49   Log-Likelihood:                 378.18
No. Observations:                8784   AIC:                            -748.4
Df Residuals:                    8780   BIC:                            -720.0
Df Model:                           3                                         
Covariance Type:            nonrobust                          

## Analysis of Regression Results: No Effect Found
Using different regression combinations of 
- GHG Intensity Last Year
- Change in GHG Intensity from 2 years ago to 1 year ago
- Square footage of building

there generally is no effect of GHG Intensity last year or change in GHG intensity from two years ago to 1 year ago. 

Interestingly but unrelatedly, it seems that larger buildings are more likely to be compliant in their reporting. The effect size is small though

## Graph to Show Averages

In [367]:


def create_scatter_with_means(df, x, y, hover_data, value_mapping, base_fontsize=12, x_label=None, y_label=None, title=None):
    """
    Create a series of side-by-side subplot scatter plots (one per unique x category),
    each with a horizontal mean line. The subplots are arranged horizontally with minimal gap.
    
    Parameters:
    - df: DataFrame containing the data.
    - x: Column name for the x-axis category variable.
    - y: Column name for the continuous y-axis variable.
    - hover_data: List of columns to display on hover.
    - value_mapping: Dictionary to map the values of the x column (often binary) to meaningful labels.
    - base_fontsize: Base font size for scaling other font sizes.
    - x_label: Label for the x-axis (overall).
    - y_label: Label for the y-axis (overall).
    - title: Main title of the entire figure.
    """
    
    # Copy and prepare the dataframe
    df = df.copy()
    df[x] = df[x].map(value_mapping)
    
    # Identify unique categories in the x variable
    categories = df[x].unique()
    categories = [cat for cat in categories if pd.notnull(cat)]  # Ensure no NaN
    
    # Calculate mean and median per category
    mean_values = df.groupby(x)[y].mean()
    median_values = df.groupby(x)[y].median()
    
    # Create subplots: one row, as many columns as unique categories
    fig = make_subplots(
        rows=1, cols=len(categories),
        horizontal_spacing=0.1,  # Narrow gap between subplots
        shared_yaxes=True,        # Share the same y-axis
        subplot_titles=categories
    )

    colors = ['rgba(0, 0, 255, 1)', 'rgba(255, 0, 0, 1)']  
    colors_t = ['rgba(0, 0, 255, 0.5)', 'rgba(255, 0, 0, 0.5)']  # Transparent versions of 'blue' and 'red'
    
    # For each category, add a scatter trace
    for i, category in enumerate(categories, start=1):

        cat_data = df[df[x] == category]
        
        # Add a small horizontal jitter around x=1 for the scatter
        jitter = np.random.uniform(0.999, 1.001, size=len(cat_data))
        
        # Create the scatter trace
        fig.add_trace(
            go.Scatter(
                x=jitter,
                y=cat_data[y],
                mode='markers',
                marker=dict(size=8, opacity=0.8, color=colors_t[i-1]),
                hovertemplate='<br>'.join([f"{col}: %{{customdata[{idx}]}}" 
                                           for idx, col in enumerate(hover_data)]) if hover_data else None,
                customdata=cat_data[hover_data] if hover_data else None,
                name = f'{y_label} <br>for "{category}"'
            ),
            row=1, col=i
        )
        
        # Add mean line
        mean_val = mean_values.loc[category]
        fig.add_hline(
            y=mean_val,
            line_dash="dash",
            line_color=colors[i-1],
            row=1, col=i,
            name = f'Mean {y_label}',
            line_width=3
        )
        
        # Add annotation for mean and median
        median_val = median_values.loc[category]
        fig.add_annotation(
            x=1.001,  # slightly to the right of the main cluster
            y=mean_val+20,
            text=f"Mean: {mean_val:.2f}<br>Median: {median_val:.2f}",
            showarrow=False,
            xanchor='left',
            yanchor='bottom',
            font=dict(size=base_fontsize * 1.2, color=colors[i-1]),
            row=1, col=i
        )
        
        # Update x-axis for this subplot (just show a single vertical line)
        fig.update_xaxes(
            showline=True,
            linecolor='black',
            zeroline=True,
            showticklabels=False,
            showgrid=False,
            range=[0.99, 1.01],   # tight range around jitter
            tickfont=dict(size=base_fontsize * 1.2),
            row=1, col=i
        )

    # Update the y-axis (shared) styling
    fig.update_yaxes(
        showline=True, 
        linecolor='black',
        showgrid=False,
        title_text=y_label, 
        title_font=dict(size=base_fontsize * 1.4),
        tickfont=dict(size=base_fontsize * 1.2),
        row=1, col=1
    )
    
    # Update the layout
    fig.update_layout(
        height=400,
        width=400*len(categories),  # adjust width based on number of categories
        title=dict(
            text=title or f'Scatterplot of {y} by {x}',
            x=0.5,
            font=dict(size=base_fontsize * 1.3)
        ),
        plot_bgcolor='white',
        margin=dict(l=40, r=40, t=150, b=80)
    )

        
    # Show the plot
    pio.show(fig)
    
    return fig

In [368]:
# Example usage:

value_mapping = {1: "Didn't Report", 0: "Reported"}
fig = create_scatter_with_means(
    df=df,
    x='non_reporting',
    y='Chng_GHGIntensity_LastYear',
    hover_data=['PropertyName', 'DataYear', 'non_reporting', 'GHGIntensity_LastYear', 'Chng_GHGIntensity_LastYear', 'GrossFloorArea_Mil'],
    value_mapping=value_mapping,
    base_fontsize=12,
    x_label='Reported This Year?',
    y_label='Change In GHG Intensity',
    title='Change In GHG Intensity (In Last 2 Years)<br> By Reporting Compliance This Year'
)


for dir in [static_blog_pth, fig_dir]:
    fig.write_html( os.path.join(dir,'change_GHG_trend_by_compliance.html'), full_html=True )


In [369]:
# Example usage:

value_mapping = {1: "Didn't Report", 0: "Reported"}
fig = create_scatter_with_means(
    df=df,
    x='non_reporting',
    y='GHGIntensity_LastYear',
    hover_data=['PropertyName', 'DataYear', 'non_reporting', 'GHGIntensity_LastYear', 'Chng_GHGIntensity_LastYear', 'GrossFloorArea_Mil'],
    value_mapping=value_mapping,
    base_fontsize=12,
    x_label='Reported This Year?',
    y_label='GHG Intensity',
    title='GHG Intensity Last Year<br> By Reporting Compliance This Year'
)


for dir in [static_blog_pth, fig_dir]:
    fig.write_html( os.path.join(dir,'GHG_last_year_by_compliance.html'), full_html=True )


In [370]:


def customizable_scatterplot(df, x_var, y_var, color_var, x_limits=None, y_limits=None, title=None):
    """
    Create a customizable scatterplot.

    Parameters:
    - df: DataFrame containing the data.
    - x_var: Column name for the x-axis.
    - y_var: Column name for the y-axis.
    - color_var: Column name for the binary variable to set discrete coloring.
    - x_limits: Tuple (min, max) to set x-axis limits.
    - y_limits: Tuple (min, max) to set y-axis limits.
    - title: Title of the plot (default: None).
    """
    # Ensure the color_var is treated as a categorical variable for discrete coloring
    df[color_var] = df[color_var].astype(str)

    # Create scatterplot
    fig = px.scatter(
        df,
        x=x_var,
        y=y_var,
        color=color_var,
        color_discrete_sequence=["blue", "orange"],  # Discrete colors for binary 0 and 1
        opacity=0.2,  # Add transparency here
        labels={x_var: x_var, y_var: y_var, color_var: color_var},
        title=title or f'Scatterplot of {y_var} vs {x_var}'
    )
    
    # Set axis limits if provided
    if x_limits:
        fig.update_xaxes(range=x_limits)
    if y_limits:
        fig.update_yaxes(range=y_limits)
    
    # Update layout for better aesthetics
    fig.update_layout(
        height=600,
        width=800,
        legend_title=color_var
    )
    
    # Show the plot
    pio.show(fig)



In [371]:
customizable_scatterplot(df,  'GHGIntensity_LastYear', 'Chng_GHGIntensity_LastYear', 'non_reporting' , 
                         x_limits =[0,40], y_limits=[-10,10], title="Scatterplot of 'Change in GHG Intensity' vs 'GHG Intensity Last Year'")

In [372]:

def hexbin_plot_with_groups(df, x_var, y_var, group_var, x_limits=None, y_limits=None, nbinsx=30, nbinsy=30, title=None):
    """
    Create a hexbin-style density heatmap with subplots for each group in a binary column.
    The density is normalized to represent the percentage of rows within each group.

    Parameters:
    - df: DataFrame containing the data.
    - x_var: Column name for the x-axis.
    - y_var: Column name for the y-axis.
    - group_var: Binary column used for creating subplots.
    - x_limits: Tuple (min, max) to set x-axis limits.
    - y_limits: Tuple (min, max) to set y-axis limits.
    - nbinsx: Number of bins along the x-axis.
    - nbinsy: Number of bins along the y-axis.
    - title: Title of the plot (default: None).
    """
    # Ensure the group_var is treated as a string for clear grouping
    df[group_var] = df[group_var].astype(str)

    # Get unique groups
    groups = df[group_var].unique()

    # Create subplots
    fig = make_subplots(
        rows=len(groups), cols=1, 
        subplot_titles=[f"{group_var} = {group}" for group in groups],
        shared_yaxes=True
    )

    for i, group in enumerate(groups):
        # Filter the DataFrame for the current group
        group_df = df[df[group_var] == group]

        # Calculate density heatmap normalized by percentage
        total_rows = len(group_df)
        heatmap = px.density_heatmap(
            group_df,
            x=x_var,
            y=y_var,
            nbinsx=nbinsx,
            nbinsy=nbinsy,
            color_continuous_scale="Viridis",
            histnorm="percent",  # Normalizes counts to percentages,
            labels={x_var: x_var, y_var: y_var}
        ).data[0]  # Extract the trace

        # Add the heatmap to the subplot
        fig.add_trace(heatmap, row=i + 1, col=1)

        # Set axis limits for this subplot if provided
        if x_limits:
            fig.update_xaxes(range=x_limits, row=i + 1, col=1)
        if y_limits:
            fig.update_yaxes(range=y_limits, row=i + 1, col=1)

    # Set x-axis and y-axis labels
    fig.update_xaxes(title_text=x_var, row=len(groups), col=1)  # Set x-axis label for the bottom plot
    fig.update_yaxes(title_text=y_var, row=int(len(groups) / 2), col=1)  # Set y-axis label for the middle plot

    # Update layout
    fig.update_layout(
        title=title or f'Density Heatmap Subplots for {group_var}',
        height=800,
        width=1200,  # Adjust width dynamically based on number of groups
        coloraxis_colorbar=dict(title="Density (%)"),  # Shared colorbar
        showlegend=True
    )

    # Show the plot
    pio.show(fig)


In [373]:
hexbin_plot_with_groups(df,  'GHGIntensity_LastYear', 'Chng_GHGIntensity_LastYear', 'non_reporting',
                         x_limits =[0,25], y_limits=[-10,10], nbinsx=1000, nbinsy=1000 )